In [55]:
import pandas as pd
import numpy as np
import bokeh as bk
import copy
import urllib
import statsmodels.api as sm
from statsmodels.stats.outliers_influence import summary_table

from bokeh.charts import Bar, Scatter, Line, output_file, show, HeatMap, Histogram
from bokeh.charts.attributes import ColorAttr, CatAttr
from bokeh.plotting  import figure, output_notebook
from bokeh.models import (HoverTool, 
                          ColumnDataSource, 
                          LinearColorMapper, 
                          CustomJS,
                          ColorBar,
                          Range1d,
                          Label)


                          
from bokeh.palettes import Viridis6, Viridis256, RdYlGn10
from bokeh.models.widgets import Slider
from bokeh.layouts import column, row
output_notebook(hide_banner=True)

import map_helper as mh


import warnings
warnings.filterwarnings('ignore')
pd.options.display.max_columns = 60

#import seaborn as sns
#import matplotlib.pyplot as plt

from IPython.lib.display import FileLink

%load_ext autoreload
%autoreload 2


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## Helper Functions for maps

In [56]:
#DFT_PTH = '/Users/Tinmar/Documents/Dev/Jupyter_nbs/hydrologic_regions_vs_counties.csv'
DFT_PTH = 'https://s3-us-west-1.amazonaws.com/tdidataset/TDI/hydrologic_regions_vs_counties.csv'


In [57]:
#DFT_PTH = '/Users/Tinmar/Documents/Dev/Jupyter_nbs/hydrologic_regions_vs_counties.csv'

def simple_county_map(dfm,key='Production',width=600,height=600,palette=Viridis256,
                      state='ca',
                      title='California Production',
                      tools="pan,wheel_zoom,box_zoom,reset,hover,save"):
    from bokeh.sampledata.us_counties import data as counties
    palette = palette[::-1]

    counties = {
        code: county for code, county in counties.items() if county["state"] == state
    }

    county_xs = [county["lons"] for county in counties.values()]
    county_ys = [county["lats"] for county in counties.values()]

    county_names = [county['name'] for county in counties.values()]
    #county_rates = [unemployment[county_id] for county_id in counties]
    county_rates = [dfm[dfm['County'] == county['name']][key] for county in counties.values()]
    color_mapper = LinearColorMapper(palette=palette,low=40,high=140)
    color_mapper = LinearColorMapper(palette=palette,low=dfm[key].min(),high=dfm[key].max())

    source = ColumnDataSource(data=dict(
        x=county_xs,
        y=county_ys,
        name=county_names,
        rate=county_rates,
        ))

    p = figure(title=title, tools=tools,
               x_axis_location=None, y_axis_location=None,
               width = width, height = height)
    p.grid.grid_line_color = None

    p.patches('x', 'y', source=source,
              fill_color={'field': 'rate', 'transform': color_mapper},
              fill_alpha=0.7, line_color="white", line_width=0.5)

    hover = p.select_one(HoverTool)
    hover.point_policy = "follow_mouse"
    hover.tooltips = [
        ("County", "@name"),
        ("{}".format(key), "@rate"),

    ]
    color_bar = ColorBar(color_mapper=color_mapper, location=(0, 0), orientation='vertical')
    p.add_layout(color_bar, 'right')
    p.toolbar_location = 'left'
    return p






def process_stats_by_counties(dfm,key='GPCD',groupkey='Year',aggfunc='mean',srcpath=DFT_PTH):
    
    # Initialize dataframe of regions and counties
    
    region_counties_df = pd.read_csv(DFT_PTH)
    region_counties_df = region_counties_df[['Hydrologic Region','County']]

    list_df = []
    for elt in dfm[groupkey].unique():
        temp_df = copy.deepcopy(region_counties_df)
        temp_df[groupkey] = elt
        list_df.append(temp_df)

    # Overwrite initial dataframe
    region_counties_df = pd.concat(list_df)

    grouped_df = dfm.groupby(['Hydrologic Region','County',groupkey])[[key]].agg(aggfunc).reset_index()

    # Adding missing groups if present
    grouped_df = grouped_df.merge(region_counties_df,on=['Hydrologic Region','County',groupkey],how='outer')

    # If counties are missing in some groups fill In Average of hydrologic region
    grouped_df[key] = grouped_df.groupby(['Hydrologic Region',groupkey]).transform(lambda x: x.fillna(x.mean()))
    return grouped_df.groupby(['County',groupkey])[key].agg(aggfunc).reset_index()
    

def add_location_to_dfm(dfm,state="ca"):
    """ Given dataframe with County field adds county boundaries in order to 
    be used in the plotting routine  """
    # Build County boundary DataFrame from bokeh county data
    from bokeh.sampledata.us_counties import data as counties
    counties = {
                code: county for code, county in counties.items() if county["state"] == state
               }
    county_xs = [county["lons"] for county in counties.values()]
    county_ys = [county["lats"] for county in counties.values()]
    county_names = [county['name'] for county in counties.values()]
    
    location_df = pd.DataFrame({'County':county_names,'x':county_xs,'y':county_ys})
    return dfm.merge(location_df,on='County',how='left')


def interactive_county_map(dfm,key='GPCD',slider_key='Year',initial_query='Year == 2014',
                    title='California GPCD',tools = "pan,wheel_zoom,box_zoom,reset,hover,save", 
                    width=600,height=600,zscale='linear'):
    """ Plots interactive map given dataframe with COunty boundary fields as wall as 
    key value and slider_key present in columns"""
    palette = Viridis256
    palette = palette[::-1]

    if zscale == 'log':
        color_mapper = LogColorMapper(palette=palette,low=dfm[key].min(),high=dfm[key].max())
    else:
        color_mapper = LinearColorMapper(palette=palette,low=dfm[key].min(),high=dfm[key].max())

    source = ColumnDataSource(dfm.dropna(), id='src')
    source_flt = ColumnDataSource(dfm.query(initial_query).fillna(-1), id='src_flt')

    p = figure(title=title, tools=tools,x_axis_location=None, y_axis_location=None,
               width = width, height=height)
    p.grid.grid_line_color = None

    p.patches('x', 'y', source=source_flt,
              fill_color={'field': key, 'transform': color_mapper},
              fill_alpha=0.7, line_color="white", line_width=0.5)

    hover = p.select_one(HoverTool)
    hover.point_policy = "follow_mouse"
    hover.tooltips = [
        ("County", "@County"),
        ("{}".format(key), "@{}".format(key)),
        ]



    callback_js_code="""
                     var orig_data = s1.data;
                     var filtered_data = s2.data;
                     var selected = cb_obj["value"];

                     for (var key in orig_data) {{
                         filtered_data[key] = [];
                         for (var i = 0; i < orig_data['County'].length; ++i) {{
                             if (orig_data['{VARNAME}'][i] === selected)  {{
                                 filtered_data[key].push(orig_data[key][i]);
                             }}
                          }}
                     }}
                     s2.trigger("change");
                     """.format(VARNAME = slider_key)

    callback = CustomJS(args=dict(s1=source,s2=source_flt), code=callback_js_code)


    slider = Slider(start=dfm[slider_key].min(), 
                    end=avg_gp[slider_key].max(), 
                    value=avg_gp[slider_key].min(), step=1, 
                    title="Select {}".format(slider_key), width=width,
                    callback=callback)


    color_bar = ColorBar(color_mapper=color_mapper, location=(0, 0), orientation='vertical')
    p.add_layout(color_bar, 'right')
    p.toolbar_location = 'left'
    return column(slider,p)


#### Other plots

## Re-Process Dataset

In [58]:
# Dataset locations

#Pre_processed_dset_pth = 'https://s3-us-west-1.amazonaws.com/tdidataset/TDI/Pre_processed_WU_dataset.csv'
#DFT_PTH = 'https://s3-us-west-1.amazonaws.com/tdidataset/TDI/hydrologic_regions_vs_counties.csv'
#County_bounday_pth = 'https://s3-us-west-1.amazonaws.com/tdidataset/TDI/counties_boundaries.hdf'

Pre_processed_dset_pth = './Pre_processed_WU_dataset.csv'
DFT_PTH = './hydrologic_regions_vs_counties.csv'
County_bounday_pth = './counties_boundaries.hdf'


In [59]:
print('Downloading preprocessed dataset from:',Pre_processed_dset_pth)
df = pd.read_csv(Pre_processed_dset_pth)
print('Downloading county boundary data from:',County_bounday_pth)
#urllib.request.urlretrieve(County_bounday_pth,'counties_boundaries.hdf')
location_df = pd.read_hdf('./counties_boundaries.hdf')
#df.head(2)

### Parse datetime

In [60]:

df['Date'] = pd.to_datetime(df.Date)
df['Date'] = df.Date.apply(lambda x: x.date())
#df['Date'] = df.Date.apply(lambda x:x.strftime("%Y-%m"))
df['Year']=df.Date.apply(lambda x: x.year)
df['Month']=df.Date.apply(lambda x: x.strftime('%b'))
df['monthcode']=df.Date.apply(lambda x: x.month)

df['Prod_res'] = df['Production']*df['% Residential']*0.01
df['Prod_ind_ag'] = df['Production']-df['Prod_res']

In [61]:
df['Conservation target'] = df['Conservation target']*100
df['Res_GPCD']=  df['GPCD']*df['% Residential']/100
df['Other_GPCD']=  df['GPCD']*(100-df['% Residential'])/100
df['Mandatory'] = df['Mandatory Restrictions'].replace(['Yes', 'No'], [1, 0])

In [62]:
estimates_california = df[['Month','Year','Production','% Residential']]
estimates_california['Production'] = estimates_california['Production']*3.0689e-6
estimates_california['Production_res'] = estimates_california['Production']*estimates_california['% Residential']/100
estimates_california['Production_other'] = estimates_california['Production']*(1-estimates_california['% Residential']/100)

In [63]:
estm = estimates_california.groupby('Year').sum().reset_index()
estm.to_dict()

{'% Residential': {0: 197220.41919999986,
  1: 340211.8771300001,
  2: 340302.12099999888,
  3: 28724.720000000001},
 'Production': {0: 3845327.2903595553,
  1: 5209076.8115657084,
  2: 5211196.2726750011,
  3: 288636.06378972897},
 'Production_other': {0: 1316172.6480713445,
  1: 1765084.3097234052,
  2: 1753445.1736391485,
  3: 90659.228451516319},
 'Production_res': {0: 2529154.6422882061,
  1: 3443992.5018423218,
  2: 3457751.0990358316,
  3: 197976.83533821252},
 'Year': {0: 2014, 1: 2015, 2: 2016, 3: 2017}}

#### 2013 production data is in another column: Stack production data in one column --> Stack them altogether


In [10]:

initcols = ['Utility_name','County','Hydrologic Region','Year','Month','% Residential']
subdf_1 = df[initcols+['Production' ]]
subdf_2 = df[initcols+['Production 2013' ]]
subdf_2.rename(columns = {'Production 2013':'Production'},inplace=True)
subdf_2['Year'] = 2013
subdf = pd.concat([subdf_1,subdf_2])
subdf['Date'] = subdf.Year.astype('str')+'-'+subdf.Month
subdf['datetime'] = pd.to_datetime(subdf['Date'])
subdf['Date'] = subdf.datetime.apply(lambda x:x.strftime("%Y-%m"))

subdf['Prod_res'] = subdf['Production']*subdf['% Residential']*0.01
subdf['Prod_ind_ag'] = subdf['Production']-subdf['Prod_res']
subdf.head(3)

Utility_name   County  Hydrologic Region  Year Month  % Residential  \
0  East Bay MUD  Alameda  San Francisco Bay  2017   Jan           62.0   
1  East Bay MUD  Alameda  San Francisco Bay  2016   Dec           62.0   
2  East Bay MUD  Alameda  San Francisco Bay  2016   Nov           61.0   

     Production     Date   datetime      Prod_res   Prod_ind_ag  
0  3.747100e+09  2017-01 2017-01-01  2.323202e+09  1.423898e+09  
1  3.767400e+09  2016-12 2016-12-01  2.335788e+09  1.431612e+09  
2  3.839100e+09  2016-11 2016-11-01  2.341851e+09  1.497249e+09

In [11]:
TOOLS = "pan,wheel_zoom,box_zoom,reset,save"
hist1 = Histogram(df, values='GPCD', color='Year',title="GPCD Distribution", 
                  width=400,height=400,fill_alpha=0.5,toolbar_location='above',tools=TOOLS,line_color=None)
hist1.legend.location = 'top_right'
palette=['grey','red', 'green', 'blue','orange']
hist2 = Histogram(subdf.query('Production <= 1.5E9'), values='Production', color='Year',
                     title="Production Distribution", width=400,height=400,toolbar_location='above',
                     tools=TOOLS,palette=palette,line_color=None)
hist2.legend.location = 'top_right'
show(row(hist1,hist2))   

### Variability of GPCD and Production over time

In [12]:
#subdf.to_csv('./Challenge/water_flask/data_fig1.csv')

In [13]:
f = subdf.groupby(['Hydrologic Region','Date']).agg('mean').reset_index()
line = Line(f, x='Date',y='Production',
            legend_sort_direction = 'ascending',
            title="Production vs Time by Hydrologic region", 
            color='Hydrologic Region', legend=True,
            width=800,height=400,tools=TOOLS)
line.legend.background_fill_alpha = 0.3
hover = line.select(dict(type=HoverTool))
#hover.tooltips = [
#    ("x", "@x"),
#    ("y", "@y"),
    #("Correlation", "@Hydrologic Region"),
#]


#palette('Viridis6')
src = ColumnDataSource(f)
tools=[HoverTool()]
p1 = Bar(src.data,'Date', values='Production', title="Total Production vs Date by Region",agg='sum', 
        stack = 'Hydrologic Region', width=800, height=500, palette = Viridis6,tools=TOOLS)
p1.legend.location = 'top_right'
p1.legend.background_fill_alpha = 0.7
show(column(line,p1))

In [14]:
key = 'Production'
avg_gp = mh.process_stats_by_counties(df,key=key,groupkey='monthcode',aggfunc='mean',srcpath=DFT_PTH)

#location_df = pd.read_hdf('./Challenge/water_flask/data/counties_boundaries.hdf')
location_df = pd.read_hdf('./counties_boundaries.hdf')
location_df.query('State == "CA"',inplace=True)
data2 = avg_gp.merge(location_df,on='County',how='left')

cal_fig = mh.interactive_county_map(data2,key=key,slider_key='monthcode',initial_query='monthcode == 1',
                             title='{} per Month by County'.format(key),
                             tools = "pan,wheel_zoom,box_zoom,reset,hover,save",
                             width=700,height=700)
show(cal_fig)

In [15]:
### Other figure

In [16]:
src = ColumnDataSource(f)
tools=[HoverTool()]
p1 = Bar(src.data,'Date', values='Production', title="Total Production vs Date by Region",agg='sum', 
        stack = 'Hydrologic Region', width=700, height=700, palette = Viridis6,tools=TOOLS)
p1.legend.location = 'top_right'
p1.legend.background_fill_alpha = 0.7
show(row(p1,cal_fig))

In [17]:

fig0 = figure(title='Mandatory Restrictions', tools="", toolbar_location=None, 
              height=400,width=700,y_axis_type="log")
qdf = df[df['Mandatory Restrictions'] == "No"]
palette=['grey','red', 'green', 'blue','orange']
for i,(k,gp) in enumerate(qdf.groupby('Year')):
    fig0.circle(gp['Conservation target'],gp['GPCD'],color=palette[i])

qdf = df[df['Mandatory Restrictions'] == "Yes"]
fig1 = figure(title='Mandatory restricions', tools="", toolbar_location=None, 
              height=400,width=700,y_axis_type="log")
palette=['grey','red', 'green', 'blue','orange']
for i,(k,gp) in enumerate(qdf.groupby('Year')):
    fig1.circle(gp['Conservation target'],gp['GPCD'],color=palette[i])

fig0.xaxis.axis_label = 'Conservation target (%)'
fig1.xaxis.axis_label = 'Conservation target (%)'
fig0.yaxis.axis_label = 'Procuction (MGal)'
fig1.yaxis.axis_label = 'Procuction (MGal)'
show(column(fig0,fig1))


### Cumulative Water savings per Year comparison DataFrame

#### Cumulative savings per Utility

In [20]:
# Year 2014 and 2017 data is incomplete let's drop them

def calculate_savings(subdf,df,key='Production'):

    #let's calculate savings from 2013 to 2016
    tmp = subdf#.query('Year != 2014 & Year != 2017')

    prod_df = tmp.groupby(['Hydrologic Region', 'County','Utility_name','Year'])[key].agg(np.mean)
    # Year 2014 and 2017 data is incomplete let's drop them

    prod_df = prod_df.unstack(['Year'])
    prod_df.columns = ['Production_{}'.format(k) for k in prod_df.columns ]
    prod_df = prod_df.reset_index()

    tmp = df
    tmp = tmp.groupby(['Hydrologic Region', 'County','Utility_name','Year'])[['Conservation target','Mandatory']].agg(np.mean)
    tmp0 = tmp.unstack(['Year'])['Conservation target']
    tmp1 = tmp.unstack(['Year'])['Mandatory']
    tmp0.columns = ['Target_{}'.format(k) for k in tmp0.columns ]
    tmp1.columns = ['Mendatory_coeff_{}'.format(k) for k in tmp1.columns ]
    tmp0 = tmp0.fillna(0)
    tmp1 = tmp1.fillna(0)
    tmp = pd.concat([tmp0,tmp1],axis=1)
    tmp = tmp.reset_index()
    tmp['Cumulative_Target'] = 1
    for k in [2014,2015,2016,2017]:
        tmp['Cumulative_Target']=tmp['Cumulative_Target']*(1-tmp['Target_{}'.format(k)]*0.01)
    tmp['Cumulative_Target'] = (1-tmp['Cumulative_Target'])*100

    comp_df = pd.merge(prod_df,tmp,on=['Hydrologic Region', 'County','Utility_name'],how='outer')
    comp_df['Savings 2013-2014'] = (comp_df.Production_2014-comp_df.Production_2013)/comp_df.Production_2013*100
    comp_df['Savings 2014-2015'] = (comp_df.Production_2015-comp_df.Production_2014)/comp_df.Production_2014*100
    comp_df['Savings 2015-2016'] = (comp_df.Production_2015-comp_df.Production_2016)/comp_df.Production_2015*100
    comp_df['Savings 2013-2016'] = (comp_df.Production_2013-comp_df.Production_2016)/comp_df.Production_2013*100
    #comp_df = comp_df[[k for k in comp_df.columns if 'Production' not in k]]
    #comp_df.head(3)
    return comp_df

In [21]:
#calculate_savings(subdf,df,key='Prod_res')

In [22]:
#from bokeh.plotting import output_file

In [53]:

def plot_fit(fig,dfm,keys=['Target_2016','Savings 2013-2016'],color='RoyalBlue'):
    x = np.array(dfm[keys[0]])
    y = np.array(dfm[keys[1]])
    X = sm.add_constant(x)


    result = sm.OLS(y, X).fit()
    st, data, ss2 = summary_table(result, alpha=0.05)
    fittedvalues = data[:,2]
    # confidence intervals
    #predict_mean_ci_low, predict_mean_ci_upp = data[:,4:6].T
    #predict_ci_low, predict_ci_upp = data[:,6:8].T

    fig.line(x,fittedvalues,color=color, line_alpha=0.8, line_width=2,legend='linear fit')

    #print(st)
    #nx = np.hstack([x,np.flipud(x)])
    #ny = np.hstack([predict_mean_ci_low,np.flipud(predict_mean_ci_upp)])
    #fig.patch(nx,ny,color='blue',alpha=0.2)

    #nx = np.hstack([x,np.flipud(x)])
    #ny = np.hstack([predict_ci_low,np.flipud(predict_ci_upp)])
    #fig.patch(nx,ny,color='blue',alpha=0.05)
    return result




keys = ['Target_2016','Savings 2013-2016']
fig = figure(title='Savings vs Targets', tools=TOOLS, toolbar_location='left', 
              height=600,width=800)

comp_df = calculate_savings(subdf,df,key='Prod_res')
corr = np.corrcoef(comp_df[keys[0]],comp_df[keys[1]])[0,1]
fig.circle(comp_df[keys[0]],comp_df[keys[1]],size=6,alpha=0.3,color='blue',legend='Prod_res')

comp_df2 = calculate_savings(subdf,df,key='Prod_ind_ag')
comp_df2 = comp_df2.dropna()
corr2 = np.corrcoef(comp_df2[keys[0]],comp_df2[keys[1]])[0,1]
fig.circle(comp_df2[keys[0]],comp_df2[keys[1]],size=6,alpha=0.3,color='red',legend='Prod_industrial_ag')

r1 = plot_fit(fig,comp_df,keys=['Target_2016','Savings 2013-2016'],color='RoyalBlue')
r2 = plot_fit(fig,comp_df2,keys=['Target_2016','Savings 2013-2016'],color='red')

fig.xaxis.axis_label = 'Cumulative Savings Target (%)'
fig.yaxis.axis_label = keys[1]+' (%)'
fig.yaxis.major_label_text_font_size = '14pt'
fig.xaxis.major_label_text_font_size = '14pt'
fig.yaxis.axis_label_text_font_size = '12pt'
fig.xaxis.axis_label_text_font_size = '12pt'
fig.y_range = Range1d(0,100)

mytext = Label(x=650, y=500, text='Correlation coeff {:.2f}'.format(corr),
               x_units='screen', y_units='screen',text_font_size='10pt')
mytext2 = Label(x=650, y=450, text='Correlation coeff {:.2f}'.format(corr2),
               x_units='screen', y_units='screen',text_font_size='10pt')

fig.add_layout(mytext)

fig.add_layout(mytext2)

fig.legend.location = "top_left"
#fig.legend.click_policy="hide"

#output_file("interactive_legend.html", title="interactive_legend.py example")

show(fig)

In [26]:
st, data, ss2 = summary_table(r1, alpha=0.05)

In [54]:
r2.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                      y   R-squared:                       0.011
Model:                            OLS   Adj. R-squared:                  0.008
Method:                 Least Squares   F-statistic:                     4.228
Date:                Thu, 06 Jul 2017   Prob (F-statistic):             0.0404
Time:                        00:15:51   Log-Likelihood:                -1543.8
No. Observations:                 396   AIC:                             3092.
Df Residuals:                     394   BIC:                             3100.
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [95.0% Conf. Int.]
------------------------------------------------------------------------------
const         19.3425      1.368     14.138      0.000        16.653    22.032
x1             0.2313      0.112      2.056      0.040         0.010     0.452
==============================================================================
Omnibus:                       78.690   Durbin-Watson:                   1.735
Prob(Omnibus):                  0.000   Jarque-Bera (JB):             1128.726
Skew:                          -0.303   Prob(JB):                    7.95e-246
Kurtosis:                      11.249   Cond. No.                         27.8
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [ ]:
def plot_correlation_matrix(dfm,threshold=0,width=600,heigth=600):
    corrm = dfm.corr().unstack().reset_index()
    cols = [k for k in corrm.columns]
    corrm['absval'] = corrm[0].abs()
    if threshold:
        corrm = corrm.query('absval >= {} & absval < 0.997'.format(threshold))
    #print(corrm)
    corrm = corrm[cols]
    factors = list(corrm.level_0.unique())
    corrm.columns = ['lv0','lv1','corr']

    TOOLS = "hover"
    fig = HeatMap(corrm, x='lv0', y='lv1', values='corr', stat=None, 
                  width=width, plot_height=heigth,tools=TOOLS, 
                  palette = RdYlGn10)
    fig.x_range.factors = fig.x_range.factors[::-1]
    hover = fig.select(dict(type=HoverTool))
    hover.tooltips = [
        ("x", "@x"),
        ("y", "@y"),
        ("Correlation", "@values"),
    ]
    fig.legend.location = None
    fig.above
    fig.title.text = 'Correlation matrix'
    fig.xaxis.major_label_text_font_size ='12pt'
    fig.yaxis.major_label_text_font_size ='12pt'
    fig.xaxis.axis_label =''
    fig.yaxis.axis_label =''
    return fig

In [ ]:
comp = comp_df[[k for k in comp_df.columns if 'Production' not in k]]
fig = plot_correlation_matrix(comp,width=800,heigth=800)
show(fig)

#### Cumulative savings per County

In [ ]:
comdf_counties = comp_df.groupby(['County']).mean().reset_index()
comdf_counties['Savings 2015-2016'] = (comdf_counties.Production_2015-comdf_counties.Production_2016)/comdf_counties.Production_2015*100
comdf_counties['Savings 2013-2016'] = (comdf_counties.Production_2013-comdf_counties.Production_2016)/comdf_counties.Production_2013*100
comdf_counties = comdf_counties.dropna()
comdf_counties.head()

In [ ]:
#df.sort('cyl', inplace=True)

list_figs = []
for i in ['Savings 2013-2016','Savings 2015-2016']:
    hist = Histogram(comp_df.dropna(subset=['Savings 2013-2016','Savings 2015-2016']), values=i, 
                 title="Distribution of {}".format(i), 
                 color= 'Hydrologic Region',
                 legend='top_left',width=450,height=400,tools='reset,pan')
    hist.legend.background_fill_alpha = 0.1
    list_figs.append(hist)
show(row(*list_figs))

comp_df.describe()

In [ ]:
## Helper Functions

def horiz_cat_barplot(dfm,keys=['Savings','Utility'],extra_key = None,
                      title='',xrange=[0,100],invert_yrange=False,color='red',axis_location="left",
                      height=500,width=500,units=''):
    factors = list(dfm[keys[1]])
    xval = dfm[keys[0]]
    
    yrange = factors
    if invert_yrange:
        yrange = factors[::-1]
    
    fig = figure(title=title, tools="", toolbar_location=None,
                y_range=yrange, x_range=xrange,y_axis_location=axis_location,height=height,width=width)

    fig.rect(xval/2, factors, width=xval, height=0.7, color=color,alpha=0.7)
    
    if extra_key:
        x = dfm[extra_key]
        fig.circle(x, factors, size=2, fill_color="orange", line_width=3, alpha=0.5)
    fig.xaxis.major_label_text_font_size = '10pt'
    fig.yaxis.major_label_text_font_size = '10pt'
    fig.yaxis.major_label_text_font_size = '10pt'
    fig.xaxis.axis_label = keys[0]+units
    return fig

def best_worst_barplot(dfm,keys=['Savings','Utility'],extra_key = None,numrecords=20,
                       title='',xrange=[0,30],invert_yrange=False,color='red',
                       axis_location="left",units='',height=500,width=500):
    
    comp_df_sorted = dfm.dropna(subset=[keys[0]]).sort_values(by=keys[0],ascending=True)
    worst_dfm = comp_df_sorted.head(numrecords)
    fig1 = horiz_cat_barplot(worst_dfm,keys=keys,
                             extra_key = None,title='Worst {}'.format(keys[0]),xrange=[-xrange[1],-xrange[0]],
                             invert_yrange=True,units=units,height=height,width=width)

    best_dfm = comp_df_sorted.tail(numrecords)
    fig2 = horiz_cat_barplot(best_dfm,keys=keys,
                             extra_key = None,title='Best {}'.format(keys[0]),color='DarkGreen',
                             axis_location="right",xrange=xrange,units=units,height=height,width=width)
    return row(fig1,fig2)
    
    


In [ ]:
comdf_counties

#### Which Counties/Utilities are amongst the worst savers the last year?

In [ ]:
fig = best_worst_barplot(comdf_counties,keys=['Savings 2015-2016','County'],extra_key = None,numrecords=15,
                      title='',xrange=[0,25],invert_yrange=False,color='red',axis_location="left",units=' (%)',width=400)
hover = fig.children[0].select(dict(type=HoverTool))
show(fig)

In [ ]:


p = simple_county_map(comdf_counties,key='Savings 2013-2016',width=600,height=600,palette=Viridis256[::-1],
                      state='ca',
                      title='California Water Savings from 2015-2016',
                      tools="pan,wheel_zoom,box_zoom,reset,hover,save")
show(p)

#### Which Utilities Specifically?


In [ ]:
fig = best_worst_barplot(comp_df,keys=['Savings 2015-2016','Utility_name'],extra_key = None,numrecords=20,
                      title='',xrange=[0,80],invert_yrange=False,color='red',axis_location="left")
show(fig)

## Were savings targets effective?

## What Factors does the production/GPCD depend on?

In [ ]:
from bokeh.palettes import RdYlGn10

In [ ]:

 
hm10 = plot_correlation_matrix(df,threshold=0)    
show(hm10)

## Predictive Modeling for total production/Region/Year
### Using linear regression with regularization (Poly features)

In [ ]:
from scipy.stats import skew
from sklearn.preprocessing import PolynomialFeatures
from sklearn.model_selection import train_test_split
from sklearn.linear_model import Ridge, RidgeCV, ElasticNet, LassoCV, LassoLarsCV
from sklearn.model_selection import cross_val_score
from sklearn.metrics import mean_squared_error

In [ ]:
# Feature Selection
X_ = df[['monthcode','Year']]
dummies = pd.get_dummies(df['Hydrologic Region'])

# Let's encode the regions
X = pd.concat([X_,dummies],axis=1)
y =np.log(df['Production']) ## To Deskew the distribution of production


In [ ]:

alphas = 10**np.linspace(8,-5,25)*0.5

model = Ridge(normalize=True)

coefs = []
errorlist = []

parameter_list = []

Degree = [1,2,3,4]
for i in Degree:
    
    polynomial_features = PolynomialFeatures(degree=i,include_bias=False)
    scaled_X = polynomial_features.fit_transform(X)
    X_train, X_test, y_train, y_test = train_test_split(scaled_X, y, test_size=0.33, random_state=40)
      
    for a in alphas:

        

        model.set_params(alpha=a)
        model.fit(X_train, y_train)
        
        # Cross validation error
        y_predicted = model.predict(X_test)
        error= mean_squared_error(y_test, y_predicted)
        
        entry = {'Degree':i, 'Alpha':a,'MSE':error, 'Coefficients':model.coef_}
        parameter_list.append(entry)
        
parameters = pd.DataFrame(parameter_list)[['Degree','Alpha','MSE','Coefficients']]

### Let's plot the cross validation error 
#### for different values of reg param alpha and polynomial degree

In [ ]:
p = figure(width=600,height=400,y_axis_type="log",x_axis_type="log",
           title='CV Mean Square Error vs Regularization param by degree',
           tools="hover,pan,box_zoom,reset")
colors = ['blue','red','green','orange','grey']

for i,(degree,gp) in enumerate(parameters.groupby('Degree')):
    p.line(gp.Alpha,gp.MSE, line_width=2,line_color=colors[i],legend="Degree: {}".format(degree))
    p.circle(gp.Alpha,gp.MSE, line_width=2,line_color=colors[i])
p.xaxis.axis_label = 'alpha'
p.yaxis.axis_label = 'Mean square error'
hover = p.select(dict(type=HoverTool))
hover.tooltips = [
    ("Alpha", "@x"),
    ("MSE", "@y"),
]
p.legend.location = 'top_left'
show(p)

### Example let's plot the data for 2016 for San Francisco Bay and compre with predictions
#### First Train model

In [ ]:
# Train the model with "optimal alpha and degree" and model set to ridge
polynomial_features = PolynomialFeatures(degree=4,include_bias=False)
scaled_X = polynomial_features.fit_transform(X)
model.set_params(alpha=8E-3)
model.fit(scaled_X, y)
y_predicted = model.predict(scaled_X)
error= mean_squared_error(y, y_predicted)
print('error:',error)

In [ ]:
#Build vecor of features
Location = 'San Francisco Bay'
Tgt_Year = 2015


dt = X[(X[Location] == 1) & (X['Year'] == 2015)]
dt = dt.head(12)
dt['Year'] = Tgt_Year
dt['monthcode'] = [1,2,3,4,5,6,7,8,9,10,11,12]

scaled_dt = polynomial_features.fit_transform(dt)
log_y_predicted = model.predict(scaled_dt)

y_predicted = np.exp(log_y_predicted)

In [ ]:
Tgt_Year = 2016

In [ ]:

#Build vecor of features
Location = 'Tulare Lake'
Tgt_Year = 2016


dt = X[(X[Location] == 1) & (X['Year'] == Tgt_Year)]
dt = dt.head(12)
dt['Year'] = Tgt_Year
dt['monthcode'] = [1,2,3,4,5,6,7,8,9,10,11,12]

scaled_dt = polynomial_features.fit_transform(dt)
log_y_predicted = model.predict(scaled_dt)

y_predicted = np.exp(log_y_predicted)

log_data = y[(X[Location] == 1) & (X['Year'] == Tgt_Year)]
data = np.exp(log_data)

mean = data.mean()
std = data.std()
p = figure(width=800,height=500,
           title='Predicted production vs month for {} for the {} region'.format(Tgt_Year,Location),
           tools="hover,pan,box_zoom,reset,save",y_range=[mean-std,mean+std])
p.line(dt['monthcode'],y_predicted, line_width=2,line_color='red',legend="Model")
p.circle(X['monthcode'],data, size=2,color='grey',legend="Data")
p.legend.location = 'top_left'
p.xaxis.axis_label = 'Month'
p.xaxis.axis_label = 'Month'
p.yaxis.axis_label = 'Prdoduction (MGal)'
p.y_range = Range1d(0,4E8)
show(p)

In [ ]:
Locations = [k for k in df['Hydrologic Region'].unique()]
palette = ['grey', 'red', 'green', 'blue', 'orange','DarkBlue','DarkViolet','Black']

In [ ]:
Locations

In [ ]:

p = figure(width=800,height=500,
               title='Predicted production vs month for {} for various CA regions'.format(Tgt_Year,Location),
               tools="hover,pan,box_zoom,reset,save",y_range=[mean-std,mean+std])
colors = palette
for i,Location in enumerate(Locations[0:8]):
#Build vecor of features


    dt = X[(X[Location] == 1) & (X['Year'] == Tgt_Year)]
    dt = dt.head(12)
    dt['Year'] = Tgt_Year
    dt['monthcode'] = [1,2,3,4,5,6,7,8,9,10,11,12]

    scaled_dt = polynomial_features.fit_transform(dt)
    log_y_predicted = model.predict(scaled_dt)

    y_predicted = np.exp(log_y_predicted)

    log_data = y[(X[Location] == 1) & (X['Year'] == Tgt_Year)]
    data = np.exp(log_data)

    mean = data.mean()
    std = data.std()
    p.line(dt['monthcode'],y_predicted, line_width=2,line_color=colors[i],legend="{}".format(Location))
    p.circle(X['monthcode'],data, size=2,color=colors[i],alpha=0.2)

p.legend.location = 'top_left'
p.legend.background_fill_alpha = 0.2
p.xaxis.axis_label = 'Month'
p.yaxis.axis_label = 'Usage (MGal)'
p.yaxis.major_label_text_font_size = '12pt'
p.xaxis.major_label_text_font_size = '12pt'
p.xaxis.axis_label_text_font_size = '12pt'
p.yaxis.axis_label_text_font_size = '12pt'
p.y_range = Range1d(0,4E8)
show(p)

In [ ]:
#To explore further

#### Notes: Run correlations with average temperatures/ water district
#### Notes: Run correlations with drought
#### Notes: Run correlations with median income per household city or by housing prices
#### Notes: Local taxes
#### Local Taxes
#### Data based on


#### Ideas: Plot histogram with map of california displayed as tooltip

# Were concservation targets effective? compare areas where those targets were zero vs others
# lowest highest comsumption in california
# per average temperatures in region and climate which might suggest water lawns
# city vs county
# paer average family size per median age

# Caluclate cumulative savings
# Water pricesP

# Map polulation increase per county
